In [1]:
import torch
import torch.nn as nn
from torchvision import datasets, transforms

C:\Users\USER-PC\anaconda3\envs\torch\lib\site-packages\torchvision\io\image.py:11: UserWarning: Failed to load image Python extension: Could not find module 'C:\Users\USER-PC\anaconda3\envs\torch\Lib\site-packages\torchvision\image.pyd' (or one of its dependencies). Try using the full path with constructor syntax.
  warn(f"Failed to load image Python extension: {e}")


In [2]:
class DenseBlockA(nn.Module):
    def __init__(self, L, k, input_channels = 12, depth = 6):
        super().__init__()
        self.L = L
        self.k = k
        self.input_channels = input_channels
        # self.module_list = self.layer
        self.total_module_list = nn.Sequential()
        self.layers = []
        self.layers.append(nn.BatchNorm2d(num_features=input_channels))
        self.layers.append(nn.ReLU())
        self.layers.append(nn.Conv2d(in_channels=input_channels, out_channels=self.k * 4, kernel_size=1, stride=1))
        self.layers.append(nn.BatchNorm2d(num_features=self.k * 4))
        self.layers.append(nn.ReLU())
        self.layers.append(nn.Conv2d(in_channels=self.k * 4, out_channels=self.k, kernel_size=3, stride=1, padding=1))

        for i in range(1, depth):
            self.layers.append(nn.BatchNorm2d(num_features=self.k))
            self.layers.append(nn.ReLU())
            self.layers.append(nn.Conv2d(in_channels=self.k, out_channels=self.k * 4, kernel_size=1, stride=1))
            self.layers.append(nn.BatchNorm2d(num_features=self.k * 4))
            self.layers.append(nn.ReLU())
            self.layers.append(nn.Conv2d(in_channels=self.k * 4, out_channels=self.k, kernel_size=3, stride=1, padding=1))

        for l_idx,layer in enumerate(self.layers):
            layer_name = "%s_%02d"%(type(layer).__name__.lower(),l_idx)
            self.total_module_list.add_module(layer_name,layer)

    def forward(self, x):
        out = self.total_module_list(x)
        return out


        

In [3]:
class DenseBlock(nn.Module):
    def __init__(self, L, k, depth = 6, i = 1):
        super().__init__()
        self.i = i
        self.L = L
        self.k = k
        self.depth = depth
        # self.module_list = self.layer
        if self.i == 1:
            self.layers = [DenseBlockA(L = self.L, k = self.k, input_channels=self.k * 2, depth = 6)]
        else:
            self.layers = [DenseBlockA(L = self.L, k = self.k, input_channels=self.k, depth = 6)]
        for j in range(1, self.L):
            if self.i == 1:
                self.layers.append(DenseBlockA(L = self.L, k = self.k, input_channels=self.k * (j+2) , depth = 6))
                # 다시 정리
            else:
                self.layers.append(DenseBlockA(L = self.L, k = self.k, input_channels=self.k * (j+1) , depth = 6))
                # 다시 정리
        self.total_module_list = nn.ModuleList(self.layers)


    def forward(self, x):
        # print(x.size())
        x_list = [x]
        # x_list.append(x)
        for i in range(self.L):
            if i == 0:
                # print(self.layer(x.size(1)))
                # print(self.layer(x.size(1))(x))
                out = self.total_module_list[i](x)
                x_list.append(out)
                # print(out.size())
                # self.total_module_list.add_module(name = f"Step {i} Module", module=self.layer(x.size(1)))
                
            else:
                cat_x = x_list[0]
                for j in range(1, len(x_list)):
                    cat_x = torch.cat((cat_x, x_list[j]), 1)
                # print(cat_x.size())
                out = self.total_module_list[i](cat_x)
                # print(out.size())
                x_list.append(out)
                # self.total_module_list.add_module(name = f"Step {i} Module", module=self.layer(cat_x.size(1)))
        # print(x_list[-1].size())
        return x_list[-1]
            
    
    # def layer(self, input_channels):
    #     layers = nn.Sequential()
    #     count = 0
    #     # print(input_channels)
    #     while count < self.depth:
    #         # print(count)
    #         if count == 0:
    #             layers.add_module(name = f"BatchNorm2d {count} - 1", module = nn.BatchNorm2d(num_features = input_channels))
    #         else:
    #             layers.add_module(name = f"BatchNorm2d {count} - 1", module = nn.BatchNorm2d(num_features = self.k))
    #         layers.add_module(name = f"ReLU {count} - 1", module = nn.ReLU())
    #         if count == 0:
    #             layers.add_module(name = f"Conv2d {count} - 1", module = nn.Conv2d(in_channels=input_channels, out_channels=4 * self.k, kernel_size=1, stride = 1))
    #         else:
    #             layers.add_module(name = f"Conv2d {count} - 1", module = nn.Conv2d(in_channels=self.k, out_channels=4 * self.k, kernel_size=1, stride = 1))
    #         layers.add_module(name = f"BatchNorm2d {count} - 2", module = nn.BatchNorm2d(num_features=4 * self.k))
    #         layers.add_module(name = f"ReLU {count} - 2", module = nn.ReLU())
    #         layers.add_module(name = f"Conv2d {count} - 2", module = nn.Conv2d(in_channels=4 * self.k, out_channels=self.k, kernel_size=3, stride = 1, padding=1))
    #         count += 1
            
    #     count = 0
    #     return layers



In [4]:
class DenseNeuralNetwork(nn.Module):
    def __init__(self, L = 40, k = 12, input_channels = 3, out_features = 1000):
        """
            This is DenseNet Prototype by kkt
            This model is needed a lot of upgrading
            Parameter:
                L : denseblock's layer length
                k : denseblock's input depth
        """
        super().__init__()
        self.L = L
        self.k = k
        self.input_channels = input_channels
        self.out_features = out_features
        # self.DenseBlock1 = DenseBlock(L=self.L, k=self.k, depth=6).to(device)
        # self.DenseBlock2 = DenseBlock(L=self.L, k=self.k, depth=12).to(device)
        # self.DenseBlock3 = DenseBlock(L=self.L, k=self.k, depth=64).to(device)
        # self.DenseBlock4 = DenseBlock(L=self.L, k=self.k, depth=48).to(device)
        self.model = nn.Sequential(
            nn.Conv2d(in_channels=self.input_channels, out_channels=self.k * 2, kernel_size=7, stride=2, padding=3), 
            nn.MaxPool2d(kernel_size=3, stride=2, padding = 1),
            DenseBlock(L=self.L, k=self.k, depth=6, i=1),
            # self.DenseBlock1,
            nn.Conv2d(in_channels=self.k, out_channels=self.k, kernel_size=1),
            nn.AvgPool2d(kernel_size=2, stride=2),
            DenseBlock(L=self.L, k=self.k, depth=12, i = 2),
            # self.DenseBlock2,
            nn.Conv2d(in_channels=self.k, out_channels=self.k, kernel_size=1),
            nn.AvgPool2d(kernel_size=2, stride=2),
            DenseBlock(L=self.L, k=self.k, depth=64, i = 3),
            # self.DenseBlock3,
            nn.Conv2d(in_channels=self.k, out_channels=self.k, kernel_size=1),
            nn.AvgPool2d(kernel_size=2, stride=2),
            DenseBlock(L=self.L, k=self.k, depth=48, i = 4),
            # self.DenseBlock4,
            nn.AvgPool2d(kernel_size=7),
            nn.Flatten(), 
            nn.Linear(in_features=self.k, out_features=self.out_features, bias=True),
            nn.Softmax(dim=1)
        )


    def forward(self, x):
        
        out = self.model(x)
        # print(out.size())
        
        # _, out = torch.max(out, 1)
        return out



In [31]:
x_torch = torch.rand(10, 3, 224, 224)
m = DenseNeuralNetwork(L = 40, k = 12)
model_pred = m.forward(x_torch)
_, y_pred = torch.max(model_pred, 1)
y_pred

torch.Size([10, 24, 56, 56])
torch.Size([10, 12, 56, 56])
torch.Size([10, 12, 28, 28])
torch.Size([10, 12, 28, 28])
torch.Size([10, 12, 14, 14])
torch.Size([10, 12, 14, 14])
torch.Size([10, 12, 7, 7])
torch.Size([10, 12, 7, 7])


tensor([726, 726, 726, 726, 726, 726, 726, 726, 281, 726])

In [32]:
for name, module in m.named_modules():
    print(name, module)

 DenseNeuralNetwork(
  (model): Sequential(
    (0): Conv2d(3, 24, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3))
    (1): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
    (2): DenseBlock(
      (total_module_list): ModuleList(
        (0): DenseBlockA(
          (total_module_list): Sequential(
            (batchnorm2d_00): BatchNorm2d(24, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
            (relu_01): ReLU()
            (conv2d_02): Conv2d(24, 48, kernel_size=(1, 1), stride=(1, 1))
            (batchnorm2d_03): BatchNorm2d(48, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
            (relu_04): ReLU()
            (conv2d_05): Conv2d(48, 12, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
            (batchnorm2d_06): BatchNorm2d(12, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
            (relu_07): ReLU()
            (conv2d_08): Conv2d(12, 48, kernel_size=(1, 1), stride=(1, 1))
        

In [33]:
for name, params in m.named_parameters():
    print(name, params.size())

model.0.weight torch.Size([24, 3, 7, 7])
model.0.bias torch.Size([24])
model.2.total_module_list.0.total_module_list.batchnorm2d_00.weight torch.Size([24])
model.2.total_module_list.0.total_module_list.batchnorm2d_00.bias torch.Size([24])
model.2.total_module_list.0.total_module_list.conv2d_02.weight torch.Size([48, 24, 1, 1])
model.2.total_module_list.0.total_module_list.conv2d_02.bias torch.Size([48])
model.2.total_module_list.0.total_module_list.batchnorm2d_03.weight torch.Size([48])
model.2.total_module_list.0.total_module_list.batchnorm2d_03.bias torch.Size([48])
model.2.total_module_list.0.total_module_list.conv2d_05.weight torch.Size([12, 48, 3, 3])
model.2.total_module_list.0.total_module_list.conv2d_05.bias torch.Size([12])
model.2.total_module_list.0.total_module_list.batchnorm2d_06.weight torch.Size([12])
model.2.total_module_list.0.total_module_list.batchnorm2d_06.bias torch.Size([12])
model.2.total_module_list.0.total_module_list.conv2d_08.weight torch.Size([48, 12, 1, 1])

In [6]:
x_torch = torch.rand(10, 3, 224, 224).to(device)
m = DenseNeuralNetwork(L = 40, k = 12).to(device)
model_pred = m.forward(x_torch)
_, y_pred = torch.max(model_pred, 1)
y_pred

torch.Size([10, 24, 56, 56])


RuntimeError: CUDA out of memory. Tried to allocate 20.00 MiB (GPU 0; 6.00 GiB total capacity; 4.11 GiB already allocated; 4.50 MiB free; 4.22 GiB reserved in total by PyTorch) If reserved memory is >> allocated memory try setting max_split_size_mb to avoid fragmentation.  See documentation for Memory Management and PYTORCH_CUDA_ALLOC_CONF

In [5]:
PATH = 'C:/Users/USER-PC/Desktop/boostcourse_github/data/CIFAR-10'
trans_cifar10 = transforms.Compose([transforms.ToTensor(), transforms.Resize((224, 224))])
cifar10_train = datasets.CIFAR10(root = PATH, train = True, transform = trans_cifar10)
cifar10_test = datasets.CIFAR10(root = PATH, train = False, transform = trans_cifar10)
cifar10_test

Dataset CIFAR10
    Number of datapoints: 10000
    Root location: C:/Users/USER-PC/Desktop/boostcourse_github/data/CIFAR-10
    Split: Test
    StandardTransform
Transform: Compose(
               ToTensor()
               Resize(size=(224, 224), interpolation=bilinear, max_size=None, antialias=None)
           )

In [6]:
BATCH_SIZE = 2
train_iter = torch.utils.data.DataLoader(cifar10_train, batch_size = BATCH_SIZE,shuffle = True )
test_iter = torch.utils.data.DataLoader(cifar10_test, batch_size = BATCH_SIZE,shuffle = False )

In [7]:
# device = torch.device('cpu')
device = torch.device('cuda:0')
import gc
gc.collect()
torch.cuda.empty_cache()

In [8]:
m = DenseNeuralNetwork(L = 40, k = 12, out_features=10).to(device)
loss = nn.CrossEntropyLoss()
optm = torch.optim.Adam(m.parameters(), lr = 1e-03)

In [9]:
from tqdm import tqdm, tqdm_notebook

In [10]:
def func_eval(model, data_iter, device):
  model.eval()
  n_correct = 0
  n_data = 0
  for batch_in, batch_out in tqdm(data_iter):
    y_target = batch_out.to(device)
    model_pred = model_pred = m.forward(batch_in.to(device))
    _, y_pred = torch.max(model_pred, 1)
    n_correct += (y_target == y_pred).sum().item()
    n_data += batch_in.size(0)

  val_accr = n_correct / n_data
  model.train()
  return val_accr

In [11]:
func_eval(m, train_iter, device)

100%|██████████| 25000/25000 [2:13:42<00:00,  3.12it/s]  


0.1